In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_001045.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003760.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_002911.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_002487.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003769.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003954.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003973.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_001086.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003945.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_003864.txt
/kaggle/input/zalo-aero/extracted_labels/extracted_labels/MobilePhone_1/frame_004794.txt
/kaggle/input/zalo-ae

In [2]:
!pip install ultralytics -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 18.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 94.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 95.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 75.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 41.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 30.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2

In [3]:
%%writefile /kaggle/working/data.yaml
path: /kaggle/working/dataset
train: images/train
val: images/val

nc: 7
names: 
  - 'Backpack'
  - 'Jacket'
  - 'Laptop'
  - 'Lifering'
  - 'MobilePhone'
  - 'Person1'
  - 'WaterBottle'

Writing /kaggle/working/data.yaml


In [4]:
import os
import glob
import random
import shutil
from pathlib import Path
from collections import defaultdict

# --- 1. ĐỊNH NGHĨA ĐƯỜNG DẪN (Giữ nguyên) ---
# Sửa lại các đường dẫn 2 tầng nếu cần
INPUT_DATASET_NAME = "zalo-aero" 
source_frames_dir = Path(f"/kaggle/input/{INPUT_DATASET_NAME}/extracted_frames/extracted_frames") 
source_labels_dir = Path(f"/kaggle/input/{INPUT_DATASET_NAME}/extracted_labels/extracted_labels") 

base_output_dir = Path("/kaggle/working/dataset")
train_images_dir = base_output_dir / "images" / "train"
val_images_dir = base_output_dir / "images" / "val"
train_labels_dir = base_output_dir / "labels" / "train"
val_labels_dir = base_output_dir / "labels" / "val"

train_images_dir.mkdir(parents=True, exist_ok=True)
val_images_dir.mkdir(parents=True, exist_ok=True)
train_labels_dir.mkdir(parents=True, exist_ok=True)
val_labels_dir.mkdir(parents=True, exist_ok=True)

# --- 2. LOGIC MỚI: CHIA 50/50 CHO TỪNG CLASS (STRATIFIED) ---
print("Bắt đầu chia 50/50 (Stratified) cho 7 classes...")

# Tạo một map các class: {'Backpack': ['Backpack_0', 'Backpack_1'], ...}
class_map = defaultdict(list)
all_sample_folders = [f for f in source_frames_dir.iterdir() if f.is_dir()]

for folder in all_sample_folders:
    # Lấy tên class (ví dụ: 'Backpack' từ 'Backpack_0')
    class_name = folder.name.split('_')[0] 
    class_map[class_name].append(folder)

train_folders = []
val_folders = []

# Duyệt qua từng class và chia
for class_name, folders in class_map.items():
    if len(folders) == 2:
        # Xáo trộn [folder_0, folder_1]
        random.shuffle(folders) 
        
        # Chia 1 cho train, 1 cho val
        train_folders.append(folders[0])
        val_folders.append(folders[1])
    else:
        # Xử lý trường hợp lạ (ví dụ: chỉ có 1 folder cho 1 class)
        print(f"Cảnh báo: Class {class_name} không có 2 thư mục. Bỏ qua...")

print(f"Tổng cộng: {len(all_sample_folders)} thư mục")
print(f"Chia {len(train_folders)} thư mục cho Train (1 của mỗi class)")
print(f"Chia {len(val_folders)} thư mục cho Validation (1 của mỗi class)")
print("---")

# --- 3. HÀM COPY FILE (Giữ nguyên) ---
def copy_files(folder_list, target_img_dir, target_label_dir):
    for folder_path in folder_list: # folder_path là một đối tượng Path
        sample_name = folder_path.name
        print(f"Processing sample folder: {sample_name}...") 
        
        # Copy Images
        for img_file in folder_path.glob("*.jpg"):
            shutil.copy(str(img_file), str(target_img_dir))
            
        # Copy Labels (nếu tồn tại)
        label_source_folder = source_labels_dir / sample_name
        if label_source_folder.exists():
            for label_file in label_source_folder.glob("*.txt"):
                shutil.copy(str(label_file), str(target_label_dir))
                
    print("---")

# --- 4. THỰC THI COPY (Giữ nguyên) ---
print("Bắt đầu copy file TRAIN...")
copy_files(train_folders, train_images_dir, train_labels_dir)

print("Bắt đầu copy file VALIDATION...")
copy_files(val_folders, val_images_dir, val_labels_dir)

print("Hoàn tất! Dữ liệu đã sẵn sàng trong thư mục '/kaggle/working/dataset'.")

Bắt đầu chia 50/50 (Stratified) cho 7 classes...
Tổng cộng: 14 thư mục
Chia 7 thư mục cho Train (1 của mỗi class)
Chia 7 thư mục cho Validation (1 của mỗi class)
---
Bắt đầu copy file TRAIN...
Processing sample folder: MobilePhone_1...
Processing sample folder: Lifering_0...
Processing sample folder: Person1_1...
Processing sample folder: WaterBottle_0...
Processing sample folder: Backpack_1...
Processing sample folder: Jacket_1...
Processing sample folder: Laptop_1...
---
Bắt đầu copy file VALIDATION...
Processing sample folder: MobilePhone_0...
Processing sample folder: Lifering_1...
Processing sample folder: Person1_0...
Processing sample folder: WaterBottle_1...
Processing sample folder: Backpack_0...
Processing sample folder: Jacket_0...
Processing sample folder: Laptop_0...
---
Hoàn tất! Dữ liệu đã sẵn sàng trong thư mục '/kaggle/working/dataset'.


In [5]:
from ultralytics import YOLO

model = YOLO('yolov8m.pt')

results = model.train(
    data='/kaggle/working/data.yaml',
    epochs=50,
    imgsz=640,
    batch=16,
    name='zalo_aero_run_2_medium'
)

print("Huấn luyện hoàn tất!")

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
Ultralytics 8.3.228 🚀 Python-3.11.13 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, compile=False, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=/kaggle/working/data.yaml, degrees=0.0, deterministic=True, device=None, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=50, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=Fals

/usr/local/lib/python3.11/dist-packages/matplotlib/colors.py:721: RuntimeWarning: invalid value encountered in less
  xa[xa < 0] = -1
/usr/local/lib/python3.11/dist-packages/matplotlib/colors.py:721: RuntimeWarning: invalid value encountered in less
  xa[xa < 0] = -1


                   all      10466       6418      0.851      0.136      0.139     0.0934
              Backpack       2785       2785          0          0          0          0
                Jacket        814        814          1          0          0          0
                Laptop        884        884      0.956      0.952      0.974      0.654
              Lifering         40         40          1          0          0          0
           MobilePhone         57         57          1          0          0          0
               Person1        517        517          1          0          0          0
           WaterBottle       1287       1321          1          0          0          0
Speed: 0.1ms preprocess, 5.4ms inference, 0.0ms loss, 0.5ms postprocess per image
Results saved to /kaggle/working/runs/detect/zalo_aero_run_2_medium
Huấn luyện hoàn tất!


In [6]:
print("Đang sao chép TẤT CẢ file từ /kaggle/working sang /kaggle/output...")

# Lệnh này copy mọi thứ (dataset, data.yaml, runs) sang nơi lưu trữ vĩnh viễn
!cp -r /kaggle/working/* /kaggle/output/

print("Hoàn tất! Mọi thứ đã được lưu an toàn.")

Đang sao chép TẤT CẢ file từ /kaggle/working sang /kaggle/output...
cp: target '/kaggle/output/' is not a directory
Hoàn tất! Mọi thứ đã được lưu an toàn.


In [7]:
!zip -r results.zip /kaggle/working/runs
print("Nén hoàn tất! File 'results.zip' đã ở trong /kaggle/working/")

  adding: kaggle/working/runs/ (stored 0%)
  adding: kaggle/working/runs/detect/ (stored 0%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/ (stored 0%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/train_batch0.jpg (deflated 4%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/train_batch1.jpg (deflated 3%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/val_batch2_labels.jpg (deflated 4%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/train_batch13081.jpg (deflated 8%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/BoxF1_curve.png (deflated 18%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/val_batch1_labels.jpg (deflated 4%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/train_batch13082.jpg (deflated 10%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/BoxPR_curve.png (deflated 21%)
  adding: kaggle/working/runs/detect/zalo_aero_run_2_medium/val_batch0_pred.jpg (deflat